In [12]:
from aerolib import *
from xfoillib import *
import pandas as pd
import numpy as np

In [13]:
def isNaN(num):
    return num != num

In [14]:
class InsufficientInputData(Exception):
    def __init__(self, text):
        self.txt = text

In [15]:
class Foil():
    def __init__(self, name):
        pass
    def get_geometry(self):
        pass
    def get_filename(self):
        pass
    

In [16]:
class Sculptor():
    def __init__(self, performance_file_name, params_file_name, settings_file_name, m):
        self.params_file_name = params_file_name
        self.geom_file_name = "GEOM.csv"
        self.aero_file_name = "AERO.csv"
        df = pd.read_csv(performance_file_name, header=None)[1:]
        self.performance = dict(zip(df[0], [float(x) for x in df[1]]))
        self.preprocess_performance()

        df = pd.read_csv(settings_file_name, header=None)[1:]
        self.settings = dict(zip(df[0], [x for x in df[1]]))
        self.preprocess_settings()

        df=pd.read_csv(params_file_name, index_col=False)
        self.params = dict(filter(lambda x: x[0][0]!="#", dict(zip(df["NAME"], [float(x) for x in df["VALUE"]])).items()))
        self.preprocess_params()

        self.geom = {}
        self.aero = {"cruise":np.nan}
        self.tom = m

    def preprocess_params(self):
        critical_params = ['CL_take_off', 'eta_prop', 'A_aft', 
                           'B_keel', 'l_stab']
        for name in critical_params:
            if isNaN(self.params.get(name, np.nan)):
                raise InsufficientInputData(f'obligatory parametr {name} not found')

    def preprocess_performance(self):
        critical_performance = ['cruise_speed', 'take_off_speed', 'flight_time']
        for name in critical_performance:
            if isNaN(self.performance.get(name, np.nan)):
                raise InsufficientInputData(f'obligatory parametr {name} not found')
    
    def preprocess_settings(self):
        if isNaN(self.settings.get('g', np.nan)):
            self.settings['g'] = 9.81
            
        if isNaN(self.settings.get('density', np.nan)):
            self.settings['density'] = 1.22

        if isNaN(self.settings.get('wire_scale_coef', np.nan)):
            self.performance['wire_scale_coef'] = 1.3
        
        critical_settings = ['dyn_viscosity', 'density', 'g', 'Re', 'M', 
                             'xfoil_max_it', 'ncr', 'alpha_min', 'alpha_max', 'alpha_step', 
                             'ar_min', 'ar_max', 'ar_delta', 'osvald_coef', 
                             'wire_scale_coef', 'XFoil_path', 'foil1_name', 'work_dir']
        for name in critical_settings:
            if isNaN(self.settings.get(name, np.nan)):
                raise InsufficientInputData(f'obligatory parametr {name} not found')

    def calculate_geometry(self):        
        self.geom["wing_area"] = wing_area(self.tom, float(self.settings["g"]),
                                           float(self.settings["density"]), 
                                           float(self.performance["take_off_speed"]), 
                                           float(self.params["CL_take_off"]))
        self.CL_cr = CL_cruise(self.tom, self.performance["cruise_speed"],
                               float(self.geom["wing_area"]), float(self.settings["g"]), 
                               float(self.settings["density"]))
        ar_step_number = int(abs(float(self.settings["ar_max"]) - float(self.settings["ar_min"])) // float(self.settings["ar_delta"]))
        
        ar_range = np.linspace(float(self.settings["ar_min"]), float(self.settings["ar_max"]), ar_step_number)
        
        self.geom["AR"] = AR_selector(ar_range, self.geom, 
                                      self.settings, self.performance, self.tom)
        self.aero["cruise"] = K_V_solver(self.geom, self.settings, 
                                         self.performance["cruise_speed"], 
                                         self.geom["AR"], self.tom)
        self.geom["ba"] = ba(self.geom["AR"], self.geom["wing_area"])
        self.geom["wingspan"] = wingspan(self.geom["AR"], self.geom["wing_area"])
        self.geom["aft_area"] = aft_area(float(self.params["A_aft"]), 
                                         self.geom["wing_area"], self.geom["ba"], 
                                         float(self.params["l_stab"]))
        self.geom["keel_area"] = keel_area(float(self.params["B_keel"]), 
                                           self.geom["wing_area"], self.geom["wingspan"], 
                                           float(self.params["l_stab"]))
        self.geom["V_dihedral"] = gamma(self.geom["keel_area"], self.geom["aft_area"])
        self.geom["Vtail_area"] = stab_area(self.geom["aft_area"], self.geom["V_dihedral"])
        self.geom["P_cruise"] = P_cruise(self.tom, self.aero["cruise"].K[0], 
                                        float(self.params["eta_prop"]), float(self.settings["g"]))
        self.geom["wire_length"] = wire_length(self.geom["wingspan"], float(self.params["l_stab"]), 
                                              float(self.settings["wire_scale_coef"]))

        self.geom["V_dihedral"] = math.degrees(gamma(self.geom["keel_area"], self.geom["aft_area"]))
        return 0
        
    def update_m(self, new_m):
        self.tom = new_m
    
    def write_geom(self):
        with open(self.geom_file_name, 'w') as f:
            f.write("%s, %s\n" % ("NAME", "VALUE"))
            for key in self.geom.keys():
                f.write("%s, %s\n" % (key, self.geom[key]))
    
    def write_aero(self):
        with open(self.aero_file_name, 'w') as f:
            f.write("%s, %s\n" % ("NAME", "VALUE"))
            for key in self.aero.keys():
                f.write("%s, %s\n" % (key, self.aero[key]))
    
    def write_info(self):
        self.write_geom()
        self.write_aero()
        
        

    def get_data_to_weigh(self):
        return [self.params_file_name, self.geom_file_name]

In [47]:
'''  
Ожидаемый формат params-csv-файла
NAME  INDEX  VALUE LINKED
0   m1    1      1            NaN
1   n1    1     10            NaN
2   m2    2      2            a1;a2
3   n2    2    100            NaN
4   m3    NaN      3          NaN
5    M    NaN   1000          a3;1/cy

Ожидаемый формат geomerty-csv-файла
NAME      VALUE
wing_area 1
ba        1
wingspan  1
AR        1

Подсчёт массы ЛА осуществляется по правилам:
 1) в ходе парсинга двух файлов (params_file, geometry_file) 
    формируется набор слагаемых, которые в сумме образуют массу ЛА
 2) все параметры из params_file, имеющие одинаковые индексы, будут перемножены, образуя слагаемое
 3) если у параметра из params_file в поле LINKED указана связанная величина 
    (или набор связанных величин) из geometry_file, 
    то этот параметр будет перемножен с ней, образуя слагаемое
    (в случае набора, слагаемым станет произведение всех величин из этого набора, умноженное на сам параметр) 
 4) если у величин указан и индекс, и связанная величина, то слагаемым станет 
    произведение всех параметров с одинаковыми индексами и всех у них указанных связанных величин
 5) в случае, если у параметра нет индекса, им становится имя параметра
 6) параметр, у которого не указан индекс и не указана связанная величина, не будет учтён при подсчёте массы
'''

def weigh(params_file_name, geometry_file_name, ask_about_no_value=True, show_keys_in_logs=False):
    geom_df = pd.read_csv(geometry_file_name, header=None).loc[1:] #удаление заголовка из DF
    geom = dict(zip(geom_df[0], geom_df[1])) #создание словаря {Cy: <val>, ...}

    #создание таблицы с колонками вида 
    #[<colomn_num>, <NAME>, <INDEX>, <VALUE>, <LINKED>]
    params = pd.read_csv(params_file_name, index_col=False) 
    params = pd.DataFrame(filter(lambda x: x["NAME"][0] != "#", [params.iloc[i] for i in range(len(params.axes[0]))])).T
    
    #создание словаря 
    #{<index>: <список значений всех параметров и связанных величин, которые в произведении образуют слагаемое>}
    multiply_dict = dict()
    multiply_dict_names = dict()
    TOM = 0
    for var in params: #итерация по колонкам; в var попадает номер колонки (colomn_num)
        params[var]["VALUE"] = float(params[var]["VALUE"])
        if isNaN(params[var]["VALUE"]):
            if ask_about_no_value:
                ans = input(f"\nУ ПАРАМЕТРА {params[var]['NAME']} нет значения - пропустить (y/n)?")
            else:
                ans = "y"
            if ans == "y":
                continue
            raise InsufficientInputData(f"no value for variable '{params[var]['NAME']}'")

        if isNaN(params[var]["INDEX"]) and isNaN(params[var]["LINKED"]):
            continue
        if not isNaN(params[var]["INDEX"]):
            index = params[var]["INDEX"]
        
        else:
            index = params[var]['NAME']

        multiply_dict[index] = multiply_dict.get(index, [])
        multiply_dict_names[index] = multiply_dict_names.get(index, [])

        #сборка слагаемого:
        #добавление параметра к тем, у которых такой же индекс
        multiply_dict[index].append(params[var]["VALUE"])
        multiply_dict_names[index].append(params[var]["NAME"])

        #добавление связанных величин
        if not isNaN(params[var]["LINKED"]):
            linked_list = "".join(params[var]["LINKED"].split()).split(";")
            try:
                linked = list(map(lambda conj: 1/float(geom[conj[2:]]) if conj[0:2] == "1/" else float(geom[conj]), linked_list))
            except KeyError as e:
                print(e)
                raise InsufficientInputData(f"for variable '{params[var]['NAME']}', '{params[var]['LINKED']}' "+\
                                                f"is specified as linked, but it is no '{params[var]['LINKED']}'"+\
                                                f" in the geom-file")
            for conj, conj_name in zip(linked, linked_list):
                multiply_dict[index].append(conj)
                multiply_dict_names[index].append(conj_name)

    #вычисление и суммирование слагаемых
    for item in multiply_dict.items():
        key, vals = item #в vals содержатся все компоненты, в произведении образующие слагаемое
        TOM += math.prod(vals)
        if show_keys_in_logs:
            print(f"[key={key}]\n + ", " * ".join(multiply_dict_names[key]) , f": {TOM}\n", sep="")
        else:
            print(" + ", " * ".join(multiply_dict_names[key]) , f": {TOM}", sep="")
    
    print(f"------------------------\nИтоговая масса: {TOM}\n------------------------\n\n")
    return TOM

In [49]:
ask_about_no_value = 0
show_keys_in_logs = 0
weigh("PARAMS.csv", "GEOM.csv", ask_about_no_value, show_keys_in_logs)

 + l_stab * tube6X5: 0.0078
 + mVTX * nVTX: 0.0318
 + mCrossfire * nCrossfire: 0.0368
 + mRunc_s4 * nRunc_s4: 0.0468
 + mReg * nReg: 0.0968
 + mAT2308 * nAT2308: 0.1548
 + mLiIon18650 * nLiIon18650: 0.2958
 + mLiIon21700 * nLiIon21700: 0.2958
 + specific_wing * wing_area * AR: 2.508788650693569
 + specific_aft * Vtail_area: 2.9813103239332106
 + mfus * nfus: 3.1313103239332105
 + mMG90 * nMG90: 3.1313103239332105
 + mES9051 * nES9051: 3.1553103239332105
 + specific_3wire * wire_length: 3.191229883251549
 + mPixhawk * nPixhawk: 3.239229883251549
 + nPito: 3.239229883251549
------------------------
Итоговая масса: 3.239229883251549
------------------------




3.239229883251549

In [46]:
'''
Модуль расчёта геометрических характеристик потребляет на вход: 
dataframe PERFORMANCE с потребными эксплуатационными характеристиками
dataframe PARAMS с параметрами электронных компонент, конструкционных материалов, аккумуляторов и т.д.
пути до файлов селиговского формата с профилем крыла wing_foil и с профилем оперения aft_foil.
TOM - значение взлётной массы в начальном приближении.

PERFORMANCE включает параметры take_off_speed, cruise_speed, flight_time, payload

PARAMS включает параметры m_FPV, m_powerplant, m_flight_control, m_fus, m_servo1, m_servo2,
line_dens_wire, line_dens_tube1, line_dens_tube2, line_dens_tube3,
area_dens_LWPLA
energy_dens_bat
number_servo1, number_servo2
l_stab
'''

# Все единицы в СИ
def inner_iteration():
    performance_file_name = "PERFORMANCE.csv"#input("имя файла performances: ")
    params_file_name = "PARAMS.csv" #input("имя файла params: ")
    settings_file_name = "SETTINGS.csv" #input("имя файла settings: ") 
    tom = 2 #input("нулевое приближение влётной массы: ")
    max_iter = 10 #input("максимальное число итераций: ")
    
    df = pd.read_csv(settings_file_name, header=None)
    tom_eps = float(dict(zip(df[0], df[1]))["tom_eps"])
    
    sculptor = Sculptor(performance_file_name, params_file_name, settings_file_name, tom)
    i = 1
    ask_about_no_value = True
    while True:
        sculptor.calculate_geometry()
        sculptor.write_info()
        pf, gf = sculptor.get_data_to_weigh()

        print(f"итерация {i}")
        new_tom = weigh(pf, gf, ask_about_no_value)
        ask_about_no_value = False
        if abs(tom - new_tom) > tom_eps:
            tom = new_tom
            sculptor.update_m(new_tom)
        else:
            print(f"сошлось на итерации: {i}")
            print("информация сохранена в файл с геометрией")
            return new_tom
        
        if i == max_iter:
            print(f"прошло {i} итераций, но расчёт всё ещё не завершён.")
            flag = 2
            while flag not in ['0', '1']:
                flag = input(f"введите 1, чтобы произвести ещё {max_iter} операций, иначе 0: ")
            if flag:
                i = 0
            else:
                print("последняя итерация геометрии сохранена")
                break
            
        i+=1
    

In [11]:
m = inner_iteration()

rm: cannot remove '/home/crucian/Desktop/aerokittes/Yura_s/OptFALT/polar.dat': No such file or directory



  XFOIL Version 6.99
  Copyright (C) 2000   Mark Drela, Harold Youngren

  This software comes with ABSOLUTELY NO WARRANTY,
    subject to the GNU General Public License.

  Caveat computor

 File  xfoil.def  not found

   QUIT    Exit program

  .OPER    Direct operating point(s)
  .MDES    Complex mapping design routine
  .QDES    Surface speed design routine
  .GDES    Geometry design routine

   SAVE f  Write airfoil to labeled coordinate file
   PSAV f  Write airfoil to plain coordinate file
   ISAV f  Write airfoil to ISES coordinate file
   MSAV f  Write airfoil to MSES coordinate file
   REVE    Reverse written-airfoil node ordering
   DELI i  Change written-airfoil file delimiters

   LOAD f  Read buffer airfoil from coordinate file
   NACA i  Set NACA 4,5-digit airfoil and buffer airfoil
   INTE    Set buffer airfoil by interpolating two airfoils
   NORM    Buffer airfoil normalization toggle
   HALF    Halve the number of points in buffer airfoil
   XYCM rr Change CM refere

rm: cannot remove '/home/crucian/Desktop/aerokittes/Yura_s/OptFALT/polar.dat': No such file or directory



 XFOIL   c>   SD   command not recognized.  Type a "?" for list

 XFOIL   c>  
 Sharp trailing edge

 Paneling parameters used...
   Number of panel nodes       160
   Panel bunching parameter    1.000
   TE/LE panel density ratio   0.150
   Refined-area/LE panel density ratio    0.200
   Top    side refined area x/c limits  1.000 1.000
   Bottom side refined area x/c limits  1.000 1.000

 XFOIL   c>  
.OPERi   c>  
 M  =    0.0000
 Re =  0.3126E+06

.OPERv   c>  
.OPERv   c>  
 M  =    0.0000
 Re =  0.3126E+06

.OPERv   c>  
 Xtr/c     =  1.0000    top    side
 Xtr/c     =  1.0000    bottom side
 NcritT    =    9.00   ( 0.070 % turb. level )
 NcritB    =    9.00   ( 0.070 % turb. level )
 Vacc      =  0.0100
 WakeL/c   =   1.000

 Klag  =  5.6000     Uxwt  =    1.00       Kdl =  0.9000
 A     =  6.7000     B     =  0.7500       KCt = 0.01485
 CtiniK=  1.8000     CtiniX=  3.3000

..VPAR   c>  
..VPAR   c>  
.OPERv   c>   Current iteration limit:          20

Enter new iteration limit 

rm: cannot remove '/home/crucian/Desktop/aerokittes/Yura_s/OptFALT/polar.dat': No such file or directory


...


Program received signal SIGFPE: Floating-point exception - erroneous arithmetic operation.

Backtrace for this error:
#0  0x7f302512ed11 in ???
#1  0x7f302512dee5 in ???
#2  0x7f3024df508f in ???
	at /build/glibc-SzIz7B/glibc-2.31/signal/../sysdeps/unix/sysv/linux/x86_64/sigaction.c:0
#3  0x55763c1a5238 in ???
#4  0x55763c1a534d in ???
#5  0x55763c15bec7 in ???
#6  0x55763c15f66c in ???
#7  0x55763c1173b1 in ???
#8  0x55763c1016be in ???
#9  0x55763c0f7748 in ???
#10  0x7f3024dd6082 in __libc_start_main
	at ../csu/libc-start.c:308
#11  0x55763c0f777d in ???
#12  0xffffffffffffffff in ???
Floating point exception (core dumped)


на одном из удлинений XFoil выдал отбивку

  XFOIL Version 6.99
  Copyright (C) 2000   Mark Drela, Harold Youngren

  This software comes with ABSOLUTELY NO WARRANTY,
    subject to the GNU General Public License.

  Caveat computor

 File  xfoil.def  not found

   QUIT    Exit program

  .OPER    Direct operating point(s)
  .MDES    Complex mapping design routine
  .QDES    Surface speed design routine
  .GDES    Geometry design routine

   SAVE f  Write airfoil to labeled coordinate file
   PSAV f  Write airfoil to plain coordinate file
   ISAV f  Write airfoil to ISES coordinate file
   MSAV f  Write airfoil to MSES coordinate file
   REVE    Reverse written-airfoil node ordering
   DELI i  Change written-airfoil file delimiters

   LOAD f  Read buffer airfoil from coordinate file
   NACA i  Set NACA 4,5-digit airfoil and buffer airfoil
   INTE    Set buffer airfoil by interpolating two airfoils
   NORM    Buffer airfoil normalization toggle
   HALF    Halve the number of points in 


Program received signal SIGFPE: Floating-point exception - erroneous arithmetic operation.

Backtrace for this error:
#0  0x7fbcb9d1ad11 in ???
#1  0x7fbcb9d19ee5 in ???
#2  0x7fbcb99e108f in ???
	at /build/glibc-SzIz7B/glibc-2.31/signal/../sysdeps/unix/sysv/linux/x86_64/sigaction.c:0
#3  0x55e4a3aae238 in ???
#4  0x55e4a3aae34d in ???
#5  0x55e4a3a64ec7 in ???
#6  0x55e4a3a6866c in ???
#7  0x55e4a3a203b1 in ???
#8  0x55e4a3a0a6be in ???
#9  0x55e4a3a00748 in ???
#10  0x7fbcb99c2082 in __libc_start_main
	at ../csu/libc-start.c:308
#11  0x55e4a3a0077d in ???
#12  0xffffffffffffffff in ???


на одном из удлинений XFoil выдал отбивку
Unexpected exception formatting exception. Falling back to standard exception


Floating point exception (core dumped)
Traceback (most recent call last):
  File "/home/crucian/.local/lib/python3.8/site-packages/IPython/core/interactiveshell.py", line 3508, in run_code
    exec(code_obj, self.user_global_ns, self.user_ns)
  File "/tmp/ipykernel_10626/789666897.py", line 1, in <module>
    inner_iteration()
  File "/tmp/ipykernel_10626/453081850.py", line 33, in inner_iteration
    sculptor.calculate_geometry()
  File "/tmp/ipykernel_10626/774885353.py", line 65, in calculate_geometry
    self.geom["AR"] = AR_selector(ar_range, self.geom,
  File "/home/crucian/Desktop/aerokittes/Yura_s/OptFALT/xfoillib.py", line 86, in AR_selector
    return df.iloc[df.K.argmax()].AR
  File "/home/crucian/.local/lib/python3.8/site-packages/pandas/core/generic.py", line 5583, in __getattr__
    return object.__getattribute__(self, name)
AttributeError: 'DataFrame' object has no attribute 'K'

During handling of the above exception, another exception occurred:

Traceback (most recent 

In [26]:
XFoil_path = "/home/crucian/Desktop/aerokittes/Yura_s/OptFALT/"
work_path = "/home/crucian/Desktop/aerokittes/Yura_s/OptFALT/"
XFoil_command_CL(16, 7, 0.15, 0.8, 1.5e-5, 0, 9, 1000, XFoil_path, work_path, "SD7037")

0

In [27]:
XFoil_run(work_path, XFoil_path)


  XFOIL Version 6.99
  Copyright (C) 2000   Mark Drela, Harold Youngren

  This software comes with ABSOLUTELY NO WARRANTY,
    subject to the GNU General Public License.

  Caveat computor

 File  xfoil.def  not found

   QUIT    Exit program

  .OPER    Direct operating point(s)
  .MDES    Complex mapping design routine
  .QDES    Surface speed design routine
  .GDES    Geometry design routine

   SAVE f  Write airfoil to labeled coordinate file
   PSAV f  Write airfoil to plain coordinate file
   ISAV f  Write airfoil to ISES coordinate file
   MSAV f  Write airfoil to MSES coordinate file
   REVE    Reverse written-airfoil node ordering
   DELI i  Change written-airfoil file delimiters

   LOAD f  Read buffer airfoil from coordinate file
   NACA i  Set NACA 4,5-digit airfoil and buffer airfoil
   INTE    Set buffer airfoil by interpolating two airfoils
   NORM    Buffer airfoil normalization toggle
   HALF    Halve the number of points in buffer airfoil
   XYCM rr Change CM refere

sh: 1: del: not found


0

In [18]:
XFoil_read(work_path)

sh: 1: del: not found


[-0.283, 0.335, 0.01165]